In [1]:
#Import the libraries we need
import pandas as pd
import numpy as np
from fredapi import Fred
import MetaTrader5 as mt5
from datetime import datetime
import time
import pytz

In [2]:
#Let's setup our FredAPI
fred = Fred(api_key="")
visa_discretionary = pd.DataFrame(fred.get_series("VISASMIDSA"),columns=["visa d"])
visa_headline      = pd.DataFrame(fred.get_series("VISASMIHSA"),columns=["visa h"])
visa_non_discretionary = pd.DataFrame(fred.get_series("VISASMINSA"),columns=["visa nd"])

In [4]:
#Initialize the terminal
mt5.initialize()

True

In [5]:
#Set timezone to UTC
timezone = pytz.timezone("Etc/UTC")

In [6]:
#Create a 'datetime' object in UTC
utc_from = datetime(2024,7,1,tzinfo=timezone)

In [7]:
#Fetch the data
eurusd = pd.DataFrame(mt5.copy_rates_from("EURUSD",mt5.TIMEFRAME_MN1,utc_from,visa_headline.shape[0]))

In [8]:
#Format the time
eurusd["time"] = pd.to_datetime(eurusd["time"],unit="s")

In [9]:
#Label the data
eurusd["target"] = np.nan
eurusd["close target"] = eurusd["close"].shift(-look_ahead)
eurusd.dropna(inplace=True)
eurusd.set_index("time",inplace=True)

In [10]:
#Let's merge the datasets
merged_data = eurusd.merge(visa_headline,right_index=True,left_index=True)
merged_data = merged_data.merge(visa_discretionary,right_index=True,left_index=True)
merged_data = merged_data.merge(visa_non_discretionary,right_index=True,left_index=True)

In [16]:
#Define the target
target = "close target"
ohlc_predictors = ["open","high","low","close","tick_volume"]
visa_predictors = ["visa d","visa h","visa nd"]
all_predictors = ohlc_predictors + visa_predictors

In [17]:
#Let's scale the data
scale_factors = pd.DataFrame(index=["mean","standard deviation"],columns=all_predictors)

for i in np.arange(0,len(all_predictors)):
    #Store the mean and standard deviation for each column
    scale_factors.iloc[0,i] = merged_data.loc[:,all_predictors[i]].mean()
    scale_factors.iloc[1,i] = merged_data.loc[:,all_predictors[i]].std()
    merged_data.loc[:,all_predictors[i]] = ((merged_data.loc[:,all_predictors[i]] - scale_factors.iloc[0,i]) / scale_factors.iloc[1,i])

scale_factors

open      high       low     close     tick_volume  \
mean                1.146552  1.165568  1.125744  1.143834  1883520.051282   
standard deviation   0.08293  0.079657  0.083896  0.080655   826680.767222   

                        visa d      visa h     visa nd  
mean                101.271017  100.848506  100.477269  
standard deviation    3.981438    6.565229    2.367663

In [18]:
#A few more libraries we need
from sklearn.neural_network import MLPRegressor
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

In [19]:
#Create train test partitions for our alternative data
train_X,test_X,train_y,test_y = train_test_split(merged_data.loc[:,all_predictors],merged_data.loc[:,"close target"],test_size=0.5,shuffle=False)

In [20]:
#Reset the index
merged_data.reset_index(inplace=True)

In [22]:
#Let's see the normalized data
merged_data

index      open      high       low     close  tick_volume  spread  \
0   2014-01-01  2.760750  2.660416  2.647981  2.537435    -1.178200       1   
1   2014-02-01  2.435776  2.722180  2.645597  2.930095    -1.417832       1   
2   2014-03-01  2.797649  2.901071  2.917004  2.895380    -0.776299       1   
3   2014-04-01  2.783178  2.824619  2.878623  3.012297    -1.131872       1   
4   2014-05-01  2.896648  2.934464  2.775281  2.722172    -1.322300       1   
..         ...       ...       ...       ...       ...          ...     ...   
112 2023-05-01 -0.548199 -0.707630 -0.741800 -0.923608    -0.826995       0   
113 2023-06-01 -0.931054 -0.808186 -0.710094 -0.654189    -0.919817       0   
114 2023-07-01 -0.671074 -0.477143 -0.505079 -0.547437    -0.909210       0   
115 2023-08-01 -0.565201 -0.741274 -0.585774 -0.738746    -0.747423       0   
116 2023-09-01 -0.751263 -0.971510 -0.917017 -1.072638    -1.040577       0   

     real_volume  target  close target    visa h    visa d   visa nd  
0              0     0.0       1.24364 -0.314554 -0.412674  0.118312  
1              0     0.0       1.20995 -0.097085  0.086045  0.376584  
2              0     0.0       1.12844 -0.289728 -0.471911 -0.187923  
3              0     0.0       1.11957 -0.008047 -0.233157  0.913288  
4              0     0.0       1.07391 -0.053343 -0.471505  0.430792  
..           ...     ...           ...       ...       ...       ...  
112            0     1.0       1.07932 -0.609887 -0.526639 -0.452507  
113            0     0.0       1.06660 -0.677476 -0.160039 -0.593825  
114            0     0.0       1.08493 -0.646435 -0.446567 -0.682647  
115            0     0.0       1.07352 -0.617400 -0.298681 -1.413451  
116            0     1.0       1.08238 -0.744559 -0.449147 -1.460138  

[117 rows x 13 columns]

In [24]:
tuner = RandomizedSearchCV(MLPRegressor(hidden_layer_sizes=(20,10,4),shuffle=False,early_stopping=True),
                           {
                               "activation": ["relu","identity","logistic","tanh"],
                               "solver": ["lbfgs","adam","sgd"],
                               "alpha": [0.1,0.01,0.001,(10.0 ** -4),(10.0 ** -5),(10.0 ** -6),(10.0 ** -7),(10.0 ** -8),(10.0 ** -9)],
                               "learning_rate": ["constant", "invscaling", "adaptive"],
                               "learning_rate_init": [0.1,0.01,0.001,(10.0 ** -4),(10.0 ** -5),(10.0 ** -6),(10.0 ** -7),(10.0 ** -8),(10.0 ** -9)],
                           },
                           cv=5,
                           n_iter=1000,
                           scoring="neg_mean_squared_error",
                           return_train_score=False,
                           n_jobs=-1
                          )

In [25]:
tuner.fit(train_X,train_y)

C:\Users\Westwood\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\model_selection\_validation.py:378: FitFailedWarning: 
42 fits failed out of a total of 5000.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
38 fits failed with the following error:
Traceback (most recent call last):
  File "C:\Users\Westwood\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\model_selection\_validation.py", line 686, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\Westwood\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py", line 749, in fit
    return self._fit(X, y, incremental=False)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

RandomizedSearchCV(cv=5,
                   estimator=MLPRegressor(early_stopping=True,
                                          hidden_layer_sizes=(20, 10, 4),
                                          shuffle=False),
                   n_iter=1000, n_jobs=-1,
                   param_distributions={'activation': ['relu', 'identity',
                                                       'logistic', 'tanh'],
                                        'alpha': [0.1, 0.01, 0.001, 0.0001,
                                                  1e-05, 1e-06, 1e-07, 1e-08,
                                                  1e-09],
                                        'learning_rate': ['constant',
                                                          'invscaling',
                                                          'adaptive'],
                                        'learning_rate_init': [0.1, 0.01, 0.001,
                                                               0.0001, 1e-05,
                                                               1e-06, 1e-07,
                                                               1e-08, 1e-09],
                                        'solver': ['lbfgs', 'adam', 'sgd']},
                   scoring='neg_mean_squared_error')

In [26]:
tuner_results = pd.DataFrame(tuner.cv_results_)
params = ["param_activation","param_solver","param_alpha","param_learning_rate","param_learning_rate_init","mean_test_score"]
tuner_results.loc[:,params].sort_values(by="mean_test_score",ascending=False)

param_activation param_solver param_alpha param_learning_rate  \
40          logistic         adam    0.000001            constant   
223         logistic         adam         0.0            constant   
954         logistic          sgd         0.0            constant   
293         logistic         adam         0.0            constant   
127         logistic         adam         0.0            adaptive   
..               ...          ...         ...                 ...   
532         identity          sgd      0.0001          invscaling   
579         identity          sgd         0.1            constant   
633         identity          sgd    0.000001            constant   
771         identity          sgd         0.0            adaptive   
811         identity          sgd      0.0001            constant   

    param_learning_rate_init  mean_test_score  
40                       0.1        -0.002079  
223                     0.01        -0.002260  
954                      0.1        -0.002262  
293                     0.01        -0.002269  
127                     0.01        -0.002601  
..                       ...              ...  
532                      0.1              NaN  
579                      0.1              NaN  
633                      0.1              NaN  
771                      0.1              NaN  
811                      0.1              NaN  

[1000 rows x 6 columns]

In [27]:
#Let's compare the default model and our customized model on the hold out set
default_model = MLPRegressor(hidden_layer_sizes=(20,10,4),shuffle=False)
customized_model = MLPRegressor(hidden_layer_sizes=(20,10,4),shuffle=False,activation=tuner.best_params_["activation"],solver=tuner.best_params_["solver"],alpha=tuner.best_params_["alpha"],learning_rate=tuner.best_params_["learning_rate"],learning_rate_init=tuner.best_params_["learning_rate_init"])

In [29]:
#The accuracy of the defualt model
default_model.fit(train_X,train_y)
mean_squared_error(test_y,default_model.predict(test_X))

C:\Users\Westwood\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.19334261927379248

In [31]:
#The accuracy of the defualt model
customized_model.fit(train_X,train_y)
mean_squared_error(test_y,customized_model.predict(test_X))

0.006138795093781729

In [37]:
#Fit the model on all the data we have
customized_model.fit(test_X,test_y)

MLPRegressor(activation='logistic', alpha=1e-06, hidden_layer_sizes=(20, 10, 4),
             learning_rate_init=0.1, shuffle=False)

In [36]:
#Convert to ONNX
from skl2onnx.common.data_types import FloatTensorType
from skl2onnx import convert_sklearn
import netron
import onnx

In [43]:
#Define the initial types
initial_types = [("float_input",FloatTensorType([1,train_X.shape[1]]))]

In [44]:
#Create the onnx representation
onnx_model = convert_sklearn(customized_model,initial_types=initial_types,target_opset=12)

In [45]:
#Save the ONNX model
onnx_model_name = "EURUSD VISA MN1 FLOAT.onnx"
onnx.save(onnx_model,onnx_model_name)

In [46]:
#View the ONNX model
netron.start(onnx_model_name)

Serving 'EURUSD VISA MN1 FLOAT.onnx' at http://localhost:8080


('localhost', 8080)